Welcome to Transport Risk Analysis for Climate AdaptaTION (TRACTION)

In [1]:
from ipyfilechooser import FileChooser
import pandas as pd
import geopandas as gpd
import os
import glob
import warnings
import logging
from tqdm import tqdm

import scripts.intersections.hazard_layers as hazard_layers
import scripts.intersections.split_networks as split_networks
#import scripts.intersections.split_networks_gpkg as split_networks_gpkg

import scripts.direct_damages.direct_damage_calculations as direct_damage_calculations
import scripts.direct_damages.expected_damages_calculations as expected_damages_calculations
import scripts.direct_damages.direct_damage_summarise as direct_damage_summarise

wd = os.getcwd()

Step 1: In the following section, fill out the requested information

In [2]:
# Edit the project name and epsg for the region of interest 
# project_name = "tanzania"
project_epsg = "32736"

In [ ]:
# Select your project folder
fc = FileChooser()
fc.show_only_dirs = True
display(fc)

In [ ]:
project_path = fc.selected
os.chdir(wd)

In [ ]:
# Locate administrative boundaries geopackage
fc = FileChooser()
fc.filter_pattern = '*.gpkg'
fc.default_path = project_path
display(fc)

In [ ]:
boundaries_path = fc.selected

In [ ]:
# Select networks folder
fc = FileChooser()
fc.show_only_dirs = True
fc.default_path = project_path
display(fc)

In [ ]:
networks_path = fc.selected

In [ ]:
# Locate road networks 
fc = FileChooser()
fc.filter_pattern = '*.gpkg'
fc.default_path = networks_path
display(fc)

In [ ]:
road_path = fc.selected

In [ ]:
# Locate rail networks 
fc = FileChooser()
fc.filter_pattern = '*.gpkg'
fc.default_path = networks_path
display(fc)

In [ ]:
rail_path = fc.selected

In [ ]:
# Locate port networks 
fc = FileChooser()
fc.filter_pattern = '*.gpkg'
fc.default_path = networks_path
display(fc)

In [ ]:
port_path = fc.selected

In [ ]:
# Locate airport networks 
fc = FileChooser()
fc.filter_pattern = '*.gpkg'
fc.default_path = networks_path
display(fc)

In [ ]:
airport_path = fc.selected

In [ ]:
# Select hazards folder (location for hazard_layers.csv)
fc = FileChooser()
fc.show_only_dirs = True
fc.default_path = project_path
display(fc)

In [ ]:
hazards_path = fc.selected

In [ ]:
# Locate flood maps folder
fc = FileChooser()
fc.show_only_dirs = True
fc.default_path = hazards_path
display(fc)

In [ ]:
floods_path = fc.selected

In [ ]:
# [For testing purposes only] Hard code all paths selected above
# Run this cell and paste it in the next one

print("project_path = \"" + project_path + "\"")
print("boundaries_path = \"" + boundaries_path + "\"")
print("networks_path = \"" + networks_path + "\"")
print("road_path = \"" + road_path + "\"")
print("rail_path = \"" + rail_path + "\"")
print("port_path = \"" + port_path + "\"")
print("airport_path = \"" + airport_path + "\"")
print("hazards_path = \"" + hazards_path + "\"")
print("floods_path = \"" + floods_path + "\"")

In [2]:
# [For testing purposes only] Hard code all paths selected above

# project_path = "/Volumes/IT/git_projects/traction/casestudies/vietnam/"
# networks_path = "/Volumes/IT/git_projects/traction/casestudies/vietnam/data/networks/"
# road_path = "/Volumes/IT/git_projects/traction/casestudies/vietnam/data/networks/road.gpkg"
# rail_path = "/Volumes/IT/git_projects/traction/casestudies/vietnam/data/networks/rail.gpkg"
# port_path = "/Volumes/IT/git_projects/traction/casestudies/vietnam/data/networks/port.gpkg"
# airport_path = "/Volumes/IT/git_projects/traction/casestudies/vietnam/data/networks/airport.gpkg"
# hazards_path = "/Volumes/IT/git_projects/traction/casestudies/vietnam/data/hazards/"
# floods_path = "/Volumes/IT/git_projects/traction/casestudies/vietnam/data/hazards/floodmaps/"

project_path = "/Volumes/IT/git_projects/east-africa-transport/"
boundaries_path = "/Volumes/IT/git_projects/east-africa-transport/data/admin_boundaries/east_africa_admin_levels/admin_levels.gpkg"
networks_path = "/Volumes/IT/git_projects/east-africa-transport/data/networks/"
road_path = "/Volumes/IT/git_projects/east-africa-transport/data/networks/road/road.gpkg"
rail_path = "/Volumes/IT/git_projects/east-africa-transport/data/networks/rail/rail.gpkg"
port_path = "/Volumes/IT/git_projects/east-africa-transport/data/networks/ports/port.gpkg"
airport_path = "/Volumes/IT/git_projects/east-africa-transport/data/networks/airports/airport.gpkg"
hazards_path = "/Volumes/IT/git_projects/east-africa-transport/data/hazards/"
floods_path = "/Volumes/IT/git_projects/east-africa-transport/data/hazards/floodmaps/"

# project_path = "/Volumes/IT/git_projects/traction/casestudies/tanzania/"
# boundaries_path = "/Volumes/IT/git_projects/traction/casestudies/tanzania/data/admin_boundaries/boundaries.gpkg"
# networks_path = "/Volumes/IT/git_projects/traction/casestudies/tanzania/data/networks/"
# road_path = "/Volumes/IT/git_projects/traction/casestudies/tanzania/data/networks/road.gpkg"
# rail_path = "/Volumes/IT/git_projects/traction/casestudies/tanzania/data/networks/rail.gpkg"
# port_path = "/Volumes/IT/git_projects/traction/casestudies/tanzania/data/networks/port.gpkg"
# airport_path = "/Volumes/IT/git_projects/traction/casestudies/tanzania/data/networks/airport.gpkg"
# hazards_path = "/Volumes/IT/git_projects/traction/casestudies/tanzania/data/hazards/"
# floods_path = "/Volumes/IT/git_projects/traction/casestudies/tanzania/data/hazards/floodmaps/"

Step 2: Prepare required paths and folders

In [3]:
# Set additional paths
layers_path = os.path.join(hazards_path,"layers")
results_path = os.path.join(project_path, "results")
data_path = os.path.join(project_path,'data')
networks_csv = os.path.join(networks_path, 'network_layers.csv')
damage_data_path = os.path.join(data_path,"damage_estimation_processing")

In [ ]:
# Create additional folders
if not os.path.exists(os.path.join(hazards_path,"layers")):
    os.makedirs(os.path.join(hazards_path,"layers"))

if not os.path.exists(os.path.join(results_path,"hazard_asset_intersection")):
    os.makedirs(os.path.join(results_path,"hazard_asset_intersection"))

if not os.path.exists(os.path.join(results_path,"direct_damages")):
    os.makedirs(os.path.join(results_path,"direct_damages"))
    
if not os.path.exists(os.path.join(results_path,"direct_damages_summary")):
    os.makedirs(os.path.join(results_path,"direct_damages_summary"))

Step 3: Prepare data for hazard intersections

In [ ]:
# Create network_layers.csv
paths = ["path"]

if road_path != None:
    paths.append(os.path.relpath(road_path, start=data_path))
if rail_path != None:
    paths.append(os.path.relpath(rail_path, start=data_path))
if port_path != None:
    paths.append(os.path.relpath(port_path, start=data_path))
if airport_path != None:
    paths.append(os.path.relpath(airport_path, start=data_path))

network_paths = pd.DataFrame(paths)
network_paths.to_csv(os.path.join(networks_path,"network_layers.csv"), index = False, header = False) 

In [ ]:
# Create hazard_layers_basic.csv
os.chdir(hazards_path)
shortcut = os.path.basename(os.path.dirname(floods_path)) + "/*.tif"
floods_files = glob.glob(shortcut)
floods_files = pd.DataFrame(floods_files)
floods_files.to_csv(os.path.join(hazards_path,"hazard_layers_basic.csv"), index = False, header = False)
os.chdir(wd)

In [ ]:
# Parse hazard layer metadata from path/filenames into hazard_layers.csv
hazard_layers.main(hazards_path)

In [ ]:
# Alternatively for Argentina 

# Read hazard_layers.csv
df = pd.read_csv(os.path.join(hazards_path,"hazard_layers.csv"))
# Save broken down by hazard, RCP, epoch

for hazard in df.hazard.unique():
    hazard_subset = df[df.hazard == hazard].copy()
    for rcp in hazard_subset.rcp.unique():
        rcp_subset = hazard_subset[hazard_subset.rcp == rcp].copy()
        for epoch in rcp_subset.epoch.unique():
            epoch_subset = rcp_subset[rcp_subset.epoch == epoch].copy()
            epoch_subset.to_csv(os.path.join(hazards_path,"layers",f"{hazard}__rcp_{rcp}__epoch_{epoch}.csv"))

In [ ]:
# Create hazard_layers_chunks.csv
os.chdir(hazards_path)
shortcut = os.path.basename(layers_path) + "/*.csv"
layers_files = glob.glob(shortcut)
layers_files = pd.DataFrame(layers_files)
layers_files.to_csv(os.path.join(hazards_path,"hazard_layers_chunks.csv"), index = False, header = False)
os.chdir(wd)

# Create a list of all layer file paths
chunks_path = os.path.join(hazards_path, 'hazard_layers_chunks.csv')
chunks_csv = open(chunks_path, "r")
chunks = [(line.strip()) for line in chunks_csv]
chunks_csv.close() 

Step 4: Create intersection geoparquets

In [5]:
# [For testing purposes only] If you just want to run the intersections without having to rerun everything above
# Define the hardcoded variables below: 

# hazards_path = "/Volumes/IT/git_projects/traction/casestudies/argentina/data/hazards/"
# networks_path = "/Volumes/IT/git_projects/traction/casestudies/argentina/data/networks/"
# networks_csv = "/Volumes/IT/git_projects/traction/casestudies/argentina/data/networks/network_layers.csv"

hazards_path = "/Volumes/IT/git_projects/east-africa-transport/data/hazards/"
networks_path = "/Volumes/IT/git_projects/east-africa-transport/data/networks/"
networks_csv = "/Volumes/IT/git_projects/east-africa-transport/data/networks/network_layers.csv"

chunks_path = os.path.join(hazards_path, 'hazard_layers_chunks.csv')
chunks_csv = open(chunks_path, "r")
chunks = [(line.strip()) for line in chunks_csv]
chunks_csv.close() 

In [7]:
# Create intersections and generate geoparquet files in results/hazard_asset_intersection folder
for i in chunks:
    hazards_csv = os.path.join(hazards_path,i)

    # Ignore writing-to-parquet warnings
    warnings.filterwarnings('ignore', message='.*initial implementation of Parquet.*')
    # Ignore reading-geopackage warnings
    warnings.filterwarnings('ignore', message='.*Sequential read of iterator was interrupted.*')

    # Enable progress_apply
    tqdm.pandas()

    # Enable info logging
    logging.basicConfig(format='%(asctime)s %(message)s', level=logging.INFO)
    logging.info("Start.")
    split_networks.main(networks_path, hazards_path, networks_csv, hazards_csv)
    logging.info("Done.")

2022-04-19 12:06:32,622 Start.
2022-04-19 12:06:32,891 Processing road.gpkg
2022-04-19 12:06:32,998 Layers: ['edges', 'nodes']
2022-04-19 12:06:32,999 Skipping road.gpkg. Already exists: /Volumes/IT/git_projects/east-africa-transport/data/networks/../../results/hazard_asset_intersection/road_splits__coastal__rcp_4.5__epoch_2030__nodes.geoparquet
2022-04-19 12:06:32,999 Skipping road.gpkg. Already exists: /Volumes/IT/git_projects/east-africa-transport/data/networks/../../results/hazard_asset_intersection/road_splits__coastal__rcp_4.5__epoch_2030__edges.geoparquet
2022-04-19 12:06:32,999 Processing rail.gpkg
2022-04-19 12:06:33,057 Layers: ['edges', 'nodes']
2022-04-19 12:06:33,252 Node CRS epsg:3857
100%|████████████████████████████████████| 6280/6280 [00:00<00:00, 95867.71it/s]
2022-04-19 12:06:33,662 Hazard coastal__rp_1__rcp_4.5__epoch_2030__conf_5__subs_nosub__model_None transform 0
2022-04-19 12:06:34,401 Hazard coastal__rp_1__rcp_4.5__epoch_2030__conf_5__subs_wtsub__model_None tra

2022-04-19 12:07:22,964 Hazard coastal__rp_1__rcp_4.5__epoch_2030__conf_95__subs_nosub__model_None transform 0
2022-04-19 12:07:23,681 Hazard coastal__rp_1__rcp_4.5__epoch_2030__conf_95__subs_wtsub__model_None transform 0
2022-04-19 12:07:24,403 Hazard coastal__rp_2__rcp_4.5__epoch_2030__conf_5__subs_nosub__model_None transform 0
2022-04-19 12:07:25,114 Hazard coastal__rp_2__rcp_4.5__epoch_2030__conf_5__subs_wtsub__model_None transform 0
2022-04-19 12:07:25,828 Hazard coastal__rp_2__rcp_4.5__epoch_2030__conf_50__subs_nosub__model_None transform 0
2022-04-19 12:07:26,611 Hazard coastal__rp_2__rcp_4.5__epoch_2030__conf_50__subs_wtsub__model_None transform 0
2022-04-19 12:07:27,330 Hazard coastal__rp_2__rcp_4.5__epoch_2030__conf_95__subs_nosub__model_None transform 0
2022-04-19 12:07:28,043 Hazard coastal__rp_2__rcp_4.5__epoch_2030__conf_95__subs_wtsub__model_None transform 0
2022-04-19 12:07:28,761 Hazard coastal__rp_5__rcp_4.5__epoch_2030__conf_5__subs_nosub__model_None transform 0
2022

2022-04-19 12:08:18,237 Hazard coastal__rp_1__rcp_4.5__epoch_2050__conf_95__subs_wtsub__model_None transform 0
2022-04-19 12:08:18,974 Hazard coastal__rp_2__rcp_4.5__epoch_2050__conf_5__subs_nosub__model_None transform 0
2022-04-19 12:08:19,691 Hazard coastal__rp_2__rcp_4.5__epoch_2050__conf_5__subs_wtsub__model_None transform 0
2022-04-19 12:08:20,397 Hazard coastal__rp_2__rcp_4.5__epoch_2050__conf_50__subs_nosub__model_None transform 0
2022-04-19 12:08:21,107 Hazard coastal__rp_2__rcp_4.5__epoch_2050__conf_50__subs_wtsub__model_None transform 0
2022-04-19 12:08:21,937 Hazard coastal__rp_2__rcp_4.5__epoch_2050__conf_95__subs_nosub__model_None transform 0
2022-04-19 12:08:22,662 Hazard coastal__rp_2__rcp_4.5__epoch_2050__conf_95__subs_wtsub__model_None transform 0
2022-04-19 12:08:23,384 Hazard coastal__rp_5__rcp_4.5__epoch_2050__conf_5__subs_nosub__model_None transform 0
2022-04-19 12:08:24,093 Hazard coastal__rp_5__rcp_4.5__epoch_2050__conf_5__subs_wtsub__model_None transform 0
2022-

2022-04-19 12:09:13,842 Hazard coastal__rp_5__rcp_4.5__epoch_2050__conf_95__subs_nosub__model_None transform 0
2022-04-19 12:09:14,635 Hazard coastal__rp_5__rcp_4.5__epoch_2050__conf_95__subs_wtsub__model_None transform 0
2022-04-19 12:09:15,358 Hazard coastal__rp_10__rcp_4.5__epoch_2050__conf_5__subs_nosub__model_None transform 0
2022-04-19 12:09:16,082 Hazard coastal__rp_10__rcp_4.5__epoch_2050__conf_5__subs_wtsub__model_None transform 0
2022-04-19 12:09:16,801 Hazard coastal__rp_10__rcp_4.5__epoch_2050__conf_50__subs_nosub__model_None transform 0
2022-04-19 12:09:17,522 Hazard coastal__rp_10__rcp_4.5__epoch_2050__conf_50__subs_wtsub__model_None transform 0
2022-04-19 12:09:18,233 Hazard coastal__rp_10__rcp_4.5__epoch_2050__conf_95__subs_nosub__model_None transform 0
2022-04-19 12:09:18,947 Hazard coastal__rp_10__rcp_4.5__epoch_2050__conf_95__subs_wtsub__model_None transform 0
2022-04-19 12:09:19,663 Hazard coastal__rp_25__rcp_4.5__epoch_2050__conf_5__subs_nosub__model_None transform

2022-04-19 12:10:04,593 Hazard coastal__rp_5__rcp_4.5__epoch_2080__conf_95__subs_wtsub__model_None transform 0
2022-04-19 12:10:05,323 Hazard coastal__rp_10__rcp_4.5__epoch_2080__conf_5__subs_nosub__model_None transform 0
2022-04-19 12:10:06,045 Hazard coastal__rp_10__rcp_4.5__epoch_2080__conf_5__subs_wtsub__model_None transform 0
2022-04-19 12:10:06,821 Hazard coastal__rp_10__rcp_4.5__epoch_2080__conf_50__subs_nosub__model_None transform 0
2022-04-19 12:10:07,564 Hazard coastal__rp_10__rcp_4.5__epoch_2080__conf_50__subs_wtsub__model_None transform 0
2022-04-19 12:10:08,285 Hazard coastal__rp_10__rcp_4.5__epoch_2080__conf_95__subs_nosub__model_None transform 0
2022-04-19 12:10:09,032 Hazard coastal__rp_10__rcp_4.5__epoch_2080__conf_95__subs_wtsub__model_None transform 0
2022-04-19 12:10:09,769 Hazard coastal__rp_25__rcp_4.5__epoch_2080__conf_5__subs_nosub__model_None transform 0
2022-04-19 12:10:10,485 Hazard coastal__rp_25__rcp_4.5__epoch_2080__conf_5__subs_wtsub__model_None transform

...

2022-04-19 12:21:39,014 Hazard river__rp_25__rcp_8.5__epoch_2030__conf_None__subs_None__model_MIROC transform 0
2022-04-19 12:21:39,742 Hazard river__rp_25__rcp_8.5__epoch_2030__conf_None__subs_None__model_NorESM1 transform 0
2022-04-19 12:21:40,464 Hazard river__rp_50__rcp_8.5__epoch_2030__conf_None__subs_None__model_GFDL transform 0
2022-04-19 12:21:41,180 Hazard river__rp_50__rcp_8.5__epoch_2030__conf_None__subs_None__model_HadGEM2 transform 0
2022-04-19 12:21:41,933 Hazard river__rp_50__rcp_8.5__epoch_2030__conf_None__subs_None__model_IPSL transform 0
2022-04-19 12:21:42,694 Hazard river__rp_50__rcp_8.5__epoch_2030__conf_None__subs_None__model_MIROC transform 0
2022-04-19 12:21:43,483 Hazard river__rp_50__rcp_8.5__epoch_2030__conf_None__subs_None__model_NorESM1 transform 0
2022-04-19 12:21:44,353 Hazard river__rp_100__rcp_8.5__epoch_2030__conf_None__subs_None__model_GFDL transform 0
2022-04-19 12:21:45,076 Hazard river__rp_100__rcp_8.5__epoch_2030__conf_None__subs_None__model_HadGE

2022-04-19 12:22:35,025 Hazard river__rp_1000__rcp_8.5__epoch_2030__conf_None__subs_None__model_MIROC transform 0
2022-04-19 12:22:35,742 Hazard river__rp_1000__rcp_8.5__epoch_2030__conf_None__subs_None__model_NorESM1 transform 0
2022-04-19 12:22:37,454 Processing port.gpkg
2022-04-19 12:22:37,504 Layers: ['nodes']
2022-04-19 12:22:37,504 Skipping port.gpkg. Already exists: /Volumes/IT/git_projects/east-africa-transport/data/networks/../../results/hazard_asset_intersection/port_splits__river__rcp_8.5__epoch_2030__nodes.geoparquet
2022-04-19 12:22:37,504 Processing airport.gpkg
2022-04-19 12:22:37,603 Layers: ['nodes']
2022-04-19 12:22:37,603 Skipping airport.gpkg. Already exists: /Volumes/IT/git_projects/east-africa-transport/data/networks/../../results/hazard_asset_intersection/airport_splits__river__rcp_8.5__epoch_2030__nodes.geoparquet
2022-04-19 12:22:37,642 Done.
2022-04-19 12:22:37,643 Start.
2022-04-19 12:22:39,476 Processing road.gpkg
2022-04-19 12:22:39,685 Layers: ['edges', '

2022-04-19 12:23:28,813 Hazard river__rp_10__rcp_8.5__epoch_2050__conf_None__subs_None__model_HadGEM2 transform 0
2022-04-19 12:23:29,529 Hazard river__rp_10__rcp_8.5__epoch_2050__conf_None__subs_None__model_IPSL transform 0
2022-04-19 12:23:30,242 Hazard river__rp_10__rcp_8.5__epoch_2050__conf_None__subs_None__model_MIROC transform 0
2022-04-19 12:23:30,966 Hazard river__rp_10__rcp_8.5__epoch_2050__conf_None__subs_None__model_NorESM1 transform 0
2022-04-19 12:23:31,690 Hazard river__rp_25__rcp_8.5__epoch_2050__conf_None__subs_None__model_GFDL transform 0
2022-04-19 12:23:33,225 Hazard river__rp_25__rcp_8.5__epoch_2050__conf_None__subs_None__model_HadGEM2 transform 0
2022-04-19 12:23:33,967 Hazard river__rp_25__rcp_8.5__epoch_2050__conf_None__subs_None__model_IPSL transform 0
2022-04-19 12:23:34,711 Hazard river__rp_25__rcp_8.5__epoch_2050__conf_None__subs_None__model_MIROC transform 0
2022-04-19 12:23:35,450 Hazard river__rp_25__rcp_8.5__epoch_2050__conf_None__subs_None__model_NorESM1

2022-04-19 12:24:19,062 Hazard river__rp_100__rcp_8.5__epoch_2080__conf_None__subs_None__model_HadGEM2 transform 0
2022-04-19 12:24:19,793 Hazard river__rp_100__rcp_8.5__epoch_2080__conf_None__subs_None__model_IPSL transform 0
2022-04-19 12:24:20,524 Hazard river__rp_100__rcp_8.5__epoch_2080__conf_None__subs_None__model_MIROC transform 0
2022-04-19 12:24:21,299 Hazard river__rp_100__rcp_8.5__epoch_2080__conf_None__subs_None__model_NorESM1 transform 0
2022-04-19 12:24:22,043 Hazard river__rp_250__rcp_8.5__epoch_2080__conf_None__subs_None__model_GFDL transform 0
2022-04-19 12:24:22,765 Hazard river__rp_250__rcp_8.5__epoch_2080__conf_None__subs_None__model_HadGEM2 transform 0
2022-04-19 12:24:23,553 Hazard river__rp_250__rcp_8.5__epoch_2080__conf_None__subs_None__model_IPSL transform 0
2022-04-19 12:24:24,272 Hazard river__rp_250__rcp_8.5__epoch_2080__conf_None__subs_None__model_MIROC transform 0
2022-04-19 12:24:24,989 Hazard river__rp_250__rcp_8.5__epoch_2080__conf_None__subs_None__mode

2022-04-19 12:25:10,568 Start.
2022-04-19 12:25:11,323 Processing road.gpkg
2022-04-19 12:25:11,547 Layers: ['edges', 'nodes']
2022-04-19 12:25:11,547 Skipping road.gpkg. Already exists: /Volumes/IT/git_projects/east-africa-transport/data/networks/../../results/hazard_asset_intersection/road_splits__river__rcp_baseline__epoch_1980__nodes.geoparquet
2022-04-19 12:25:11,547 Skipping road.gpkg. Already exists: /Volumes/IT/git_projects/east-africa-transport/data/networks/../../results/hazard_asset_intersection/road_splits__river__rcp_baseline__epoch_1980__edges.geoparquet
2022-04-19 12:25:11,548 Processing rail.gpkg
2022-04-19 12:25:11,771 Layers: ['edges', 'nodes']
2022-04-19 12:25:12,195 Node CRS epsg:3857
100%|███████████████████████████████████| 6280/6280 [00:00<00:00, 112134.75it/s]
2022-04-19 12:25:12,555 Hazard river__rp_2__rcp_baseline__epoch_1980__conf_None__subs_None__model_baseline transform 0
2022-04-19 12:25:13,444 Hazard river__rp_5__rcp_baseline__epoch_1980__conf_None__subs_

Step 5: Calculate direct damages and expected annual damages

In [7]:
# Run direct_damage_calculations.py
direct_damage_calculations.main(damage_data_path, layers_path, data_path, results_path, project_epsg)

100%|██████████████████████████████████| 59336/59336 [00:00<00:00, 92816.04it/s]
/Users/dianajaramillo/opt/anaconda3/envs/myenv/lib/python3.9/site-packages/pyproj/crs/crs.py:131: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
100%|████████████████████████████████████████| 17/17 [00:00<00:00, 22345.09it/s]
/Users/dianajaramillo/opt/anaconda3/envs/myenv/lib/python3.9/site-packages/pyproj/crs/crs.py:131: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_st

100%|████████████████████████████████████████| 41/41 [00:00<00:00, 37547.26it/s]
/Users/dianajaramillo/opt/anaconda3/envs/myenv/lib/python3.9/site-packages/pyproj/crs/crs.py:131: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
100%|████████████████████████████████████████| 41/41 [00:00<00:00, 38214.77it/s]
/Users/dianajaramillo/opt/anaconda3/envs/myenv/lib/python3.9/site-packages/pyproj/crs/crs.py:131: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_st

100%|████████████████████████████████████████| 42/42 [00:00<00:00, 37528.92it/s]
/Users/dianajaramillo/opt/anaconda3/envs/myenv/lib/python3.9/site-packages/pyproj/crs/crs.py:131: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
100%|████████████████████████████████████████| 42/42 [00:00<00:00, 37770.32it/s]
/Users/dianajaramillo/opt/anaconda3/envs/myenv/lib/python3.9/site-packages/pyproj/crs/crs.py:131: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_st

100%|████████████████████████████████████████| 41/41 [00:00<00:00, 37786.52it/s]
/Users/dianajaramillo/opt/anaconda3/envs/myenv/lib/python3.9/site-packages/pyproj/crs/crs.py:131: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
100%|████████████████████████████████████████| 42/42 [00:00<00:00, 36876.86it/s]
/Users/dianajaramillo/opt/anaconda3/envs/myenv/lib/python3.9/site-packages/pyproj/crs/crs.py:131: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_st

100%|████████████████████████████████████████| 42/42 [00:00<00:00, 38387.62it/s]
/Users/dianajaramillo/opt/anaconda3/envs/myenv/lib/python3.9/site-packages/pyproj/crs/crs.py:131: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
100%|████████████████████████████████████████| 42/42 [00:00<00:00, 38606.35it/s]
/Users/dianajaramillo/opt/anaconda3/envs/myenv/lib/python3.9/site-packages/pyproj/crs/crs.py:131: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_st

...

100%|████████████████████████████████████| 6906/6906 [00:00<00:00, 60866.72it/s]
/Users/dianajaramillo/opt/anaconda3/envs/myenv/lib/python3.9/site-packages/pyproj/crs/crs.py:131: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
100%|████████████████████████████████████| 8795/8795 [00:00<00:00, 61652.49it/s]
/Users/dianajaramillo/opt/anaconda3/envs/myenv/lib/python3.9/site-packages/pyproj/crs/crs.py:131: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_st

100%|████████████████████████████████████| 5284/5284 [00:00<00:00, 59618.67it/s]
/Users/dianajaramillo/opt/anaconda3/envs/myenv/lib/python3.9/site-packages/pyproj/crs/crs.py:131: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
100%|████████████████████████████████████| 7008/7008 [00:00<00:00, 60820.09it/s]
/Users/dianajaramillo/opt/anaconda3/envs/myenv/lib/python3.9/site-packages/pyproj/crs/crs.py:131: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_st

100%|██████████████████████████████████| 10866/10866 [00:00<00:00, 62314.72it/s]
/Users/dianajaramillo/opt/anaconda3/envs/myenv/lib/python3.9/site-packages/pyproj/crs/crs.py:131: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
100%|████████████████████████████████████| 7272/7272 [00:00<00:00, 61458.97it/s]
/Users/dianajaramillo/opt/anaconda3/envs/myenv/lib/python3.9/site-packages/pyproj/crs/crs.py:131: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_st

* No river intersections with road edges


/Users/dianajaramillo/opt/anaconda3/envs/myenv/lib/python3.9/site-packages/pyproj/crs/crs.py:131: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
100%|████████████████████████████████████| 5152/5152 [00:00<00:00, 59522.84it/s]
/Users/dianajaramillo/opt/anaconda3/envs/myenv/lib/python3.9/site-packages/pyproj/crs/crs.py:131: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
100%|████████████████████████████████████| 5369/5369 [00:00<00:00, 57679.62

In [8]:
# Run expected_damages_calculations.py
expected_damages_calculations.main(damage_data_path, results_path)

/var/folders/8_/bfhfn0m14qx3pjj7l2khj6640000gn/T/ipykernel_60702/530228750.py:2: DtypeWarning: Columns (5,6,8) have mixed types.Specify dtype option on import or set low_memory=False.
  expected_damages_calculations.main(damage_data_path, results_path)
/Volumes/IT/git_projects/traction/scripts/direct_damages/expected_damages_calculations.py:42: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  damages['probability'] = 1.0/damages['rp']
100%|████████████████████████████████████████| 42/42 [00:00<00:00, 13681.33it/s]


100%|████████████████████████████████████| 3563/3563 [00:00<00:00, 17407.48it/s]


100%|████████████████████████████████████████| 37/37 [00:00<00:00, 13104.99it/s]


100%|████████████████████████████████████| 4721/4721 [00:00<00:00, 17257.08it/s]


100%|████████████████████████████████████| 4218/4218 [00:00<00:00, 24966.66it/s]


* Done with road edges


In [9]:
# Run direct_damage_summarise.py
direct_damage_summarise.main(damage_data_path, results_path)

/var/folders/8_/bfhfn0m14qx3pjj7l2khj6640000gn/T/ipykernel_60702/2919340700.py:2: DtypeWarning: Columns (5,6,8) have mixed types.Specify dtype option on import or set low_memory=False.
  direct_damage_summarise.main(damage_data_path, results_path)


* Done with creating list of all dataframes
* Done with concatinating all dataframes
* Done with road edges direct_damages


/var/folders/8_/bfhfn0m14qx3pjj7l2khj6640000gn/T/ipykernel_60702/2919340700.py:2: DtypeWarning: Columns (5) have mixed types.Specify dtype option on import or set low_memory=False.
  direct_damage_summarise.main(damage_data_path, results_path)


* Done with creating list of all dataframes
* Done with concatinating all dataframes
* Done with road edges EAD
